In [1]:
import timm
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader
from torchvision import transforms, datasets
import os
import pandas as pd
from PIL import Image
from torch.utils.data import Dataset

In [2]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f'Using device: {device}')

Using device: cuda


In [4]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# os.environ['KAGGLE_CONFIG_DIR'] = "/content"

In [ ]:
# %cd /content/drive/MyDrive/
# !kaggle datasets download -d ashery/chexpert -p chexpert_data

In [5]:
model = timm.create_model('vit_base_patch16_224', pretrained=True)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


model.safetensors:   0%|          | 0.00/346M [00:00<?, ?B/s]

In [17]:
class CheXpertDataset(Dataset):
    def __init__(self, csv_file, img_dir, transform=None):
        self.labels_df = pd.read_csv(csv_file)
        self.img_dir = img_dir
        self.transform = transform

    def __len__(self):
        return len(self.labels_df)

    def __getitem__(self, idx):
        img_rel_path = self.labels_df.iloc[idx]['Path']
        relative_path = os.path.relpath(img_rel_path, start='train')
        img_path = os.path.join(self.img_dir, relative_path)

        try:
            image = Image.open(img_path).convert('RGB')
        except Exception as e:
            print(f"[WARNING] Could not load image: {img_path} -- {e}")
            image = Image.new('RGB', (244, 244), (0, 0, 0))  # تصویر مشکی جایگزین

        if self.transform:
            image = self.transform(image)

        labels = self.labels_df.iloc[idx][['Atelectasis', 'Cardiomegaly', 'Consolidation', 'Edema', 'Pleural Effusion']].fillna(0).values.astype('float32')

        return image, labels


In [26]:
transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize([0.5], [0.5])
])

In [27]:
train_dataset = CheXpertDataset(
    csv_file='/content/drive/MyDrive/chexpert_data_v2/train.csv',
    img_dir='/content/drive/MyDrive/chexpert_data_v2_resized/train',
    transform=transform
)

In [28]:
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)

In [29]:
val_dataset = CheXpertDataset(
    csv_file='/content/drive/MyDrive/chexpert_data_v2/valid.csv',
    img_dir='/content/drive/MyDrive/chexpert_data_v2_resized/valid',
    transform=transform
)

In [30]:
val_loader = DataLoader(val_dataset, batch_size=32, shuffle=False)

In [31]:
model = model.to(device)

In [32]:
model.head = nn.Linear(model.head.in_features, 5)
model = model.to(device)

In [33]:
criterion = nn.BCEWithLogitsLoss()
optimizer = optim.Adam(model.parameters(), lr=1e-4)

In [34]:
# num_epochs = 5

# for epoch in range(num_epochs):
#     model.train()
#     running_loss = 0.0
#     for images, labels in train_loader:
#         images = images.to(device)
#         labels = labels.to(device)

#         optimizer.zero_grad()
#         outputs = model(images)
#         loss = criterion(outputs, labels)
#         loss.backward()
#         optimizer.step()

#         running_loss += loss.item()

#     print(f"Epoch [{epoch+1}/{num_epochs}], Loss: {running_loss/len(train_loader):.4f}")


[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient54849/study1/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient54849/study1/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient39960/study2/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient39960/study2/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient16411/study8/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient16411/study8/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDri

/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = self.labels_df.iloc[idx][['Atelectasis', 'Cardiomegaly', 'Consolidation', 'Edema', 'Pleural Effusion']].fillna(0).values.astype('float32')
/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = self.labels_df.iloc[idx][['Atelectasis', 'Cardiomegaly', 'Consolidation', 'Edema', 'Pleural Effusion']].fillna(0).values.astype('float32')
/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .f

[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient48243/study3/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient48243/study3/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient14003/study2/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient14003/study2/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient17630/study3/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient17630/study3/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDri

/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = self.labels_df.iloc[idx][['Atelectasis', 'Cardiomegaly', 'Consolidation', 'Edema', 'Pleural Effusion']].fillna(0).values.astype('float32')
/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = self.labels_df.iloc[idx][['Atelectasis', 'Cardiomegaly', 'Consolidation', 'Edema', 'Pleural Effusion']].fillna(0).values.astype('float32')
/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .f

[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient01688/study4/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient01688/study4/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient62059/study1/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient62059/study1/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient43014/study1/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient43014/study1/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDri

...

[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient40487/study15/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient40487/study15/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient21514/study1/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient21514/study1/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient14350/study1/view2_lateral.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient14350/study1/view2_lateral.jpg'
[WARNING] Could not load image: /content/drive/MyD

/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = self.labels_df.iloc[idx][['Atelectasis', 'Cardiomegaly', 'Consolidation', 'Edema', 'Pleural Effusion']].fillna(0).values.astype('float32')
/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = self.labels_df.iloc[idx][['Atelectasis', 'Cardiomegaly', 'Consolidation', 'Edema', 'Pleural Effusion']].fillna(0).values.astype('float32')
/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .f

[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient57621/study1/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient57621/study1/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient42447/study2/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient42447/study2/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient16523/study10/view1_frontal.jpg -- [Errno 2] No such file or directory: '/content/drive/MyDrive/chexpert_data_v2_resized/train/../CheXpert-v1.0-small/train/patient16523/study10/view1_frontal.jpg'
[WARNING] Could not load image: /content/drive/MyD

/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = self.labels_df.iloc[idx][['Atelectasis', 'Cardiomegaly', 'Consolidation', 'Edema', 'Pleural Effusion']].fillna(0).values.astype('float32')
/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  labels = self.labels_df.iloc[idx][['Atelectasis', 'Cardiomegaly', 'Consolidation', 'Edema', 'Pleural Effusion']].fillna(0).values.astype('float32')
/tmp/ipython-input-17-1896236660.py:25: FutureWarning: Downcasting object dtype arrays on .f

KeyboardInterrupt: 